In [1]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline

from fastai.learner import *

import torchtext
from torchtext import vocab, data
from torchtext.datasets import language_modeling

from fastai.rnn_reg import *
from fastai.rnn_train import *
from fastai.nlp import *
from fastai.lm_rnn import *

import dill as pickle
import pandas as pd
import numpy as np

OSError: Can't find model 'en'

In [2]:
PATH='data/spooky-author-identification/'


%ls {PATH}

models/                                    testData.txt   train.zip
open?id=1yRWGUKpAl9qxFWkkhsbSf_N1fSWTIXty  test.zip       view?usp=sharing
sample_submission.csv                      tmp/           weights/
sample_submission.zip                      train.csv
test.csv                                   trainData.txt


In [3]:
def save_data(df, file_train):
    trainData =""
    for idx, row in df.iterrows():
        data = row['text']
        if trainData == "":
            trainData= data
        else :
            trainData=trainData + " " + data

    file_train.write(trainData)
    file_train.close()
    return trainData

In [4]:
file_train= open(f'{PATH}trainData.txt','w') 

In [5]:
df_train = pd.read_csv(f'{PATH}train.csv')

In [6]:
train_data= save_data(df_train,file_train)

In [7]:
df_test = pd.read_csv(f'{PATH}test.csv')

In [8]:
file_test= open(f'{PATH}testData.txt','w') 

In [9]:
test_data= save_data(df_test,file_test)

In [10]:
' '.join(spacy_tok(train_data))

'This process , however , afforded me no means of ascertaining the dimensions of my dungeon ; as I might make its circuit , and return to the point whence I set out , without being aware of the fact ; so perfectly uniform seemed the wall . It never once occurred to me that the fumbling might be a mere mistake . In his left hand was a gold snuff box , from which , as he capered down the hill , cutting all manner of fantastic steps , he took snuff incessantly with an air of the greatest possible self satisfaction . How lovely is spring As we looked from Windsor Terrace on the sixteen fertile counties spread beneath , speckled by happy cottages and wealthier towns , all looked as in former years , heart cheering and fair . Finding nothing else , not even gold , the Superintendent abandoned his attempts ; but a perplexed look occasionally steals over his countenance as he sits thinking at his desk . A youth passed in solitude , my best years spent under your gentle and feminine fosterage ,

In [11]:
TEXT = data.Field(lower=True, tokenize=spacy_tok)

In [12]:
TRN_PATH =  'trainData.txt'
VAL_PATH = 'testData.txt'
TRN = f'{PATH}trainData.txt'
VAL = f'{PATH}testData.txt'

In [13]:
bs=2; bptt=70

In [14]:
FILES = dict(train=TRN_PATH, validation=VAL_PATH, test=VAL_PATH)


In [15]:
md = LanguageModelData.from_text_files(PATH, TEXT, **FILES, bs=bs, bptt=bptt, min_freq=10)

In [17]:
pickle.dump(TEXT, open(f'{PATH}models/TEXT.pkl','wb'))

In [16]:
em_sz = 20  # size of each embedding vector
nh = 50     # number of hidden activations per layer
nl = 3       # number of layers

In [17]:
opt_fn = partial(optim.Adam, betas=(0.7, 0.99))

In [18]:
learner = md.get_model(opt_fn, em_sz, nh, nl,
               dropouti=0.05, dropout=0.05, wdrop=0.1, dropoute=0.02, dropouth=0.05)
learner.reg_fn = partial(seq2seq_reg, alpha=2, beta=1)
learner.clip=0.3

In [19]:
learner.fit(3e-3, 1, wds=1e-6, cycle_len=1, cycle_mult=1)

HBox(children=(IntProgress(value=0, description='Epoch', max=1), HTML(value='')))

[ 0.       5.42404  5.37824]                                  



In [20]:
learner.save_encoder('lang-model-spooky1')

In [21]:
learner.load_encoder('lang-model-spooky1')

In [22]:
TEXT = pickle.load(open(f'{PATH}models/TEXT.pkl','rb'))

In [23]:
msk = np.random.rand(len(df_train)) < 0.9
df_val = df_train[~msk].reset_index()
df_train = df_train[msk].reset_index()

In [24]:
df = {'train': df_train, 'val': df_val, 'test': df_test}


In [25]:
LABEL = data.Field(sequential=False)


In [26]:
df_train.head()

index       id                                               text author
0      0  id26305  This process, however, afforded me no means of...    EAP
1      1  id17569  It never once occurred to me that the fumbling...    HPL
2      3  id27763  How lovely is spring As we looked from Windsor...    MWS
3      4  id12958  Finding nothing else, not even gold, the Super...    HPL
4      5  id22965  A youth passed in solitude, my best years spen...    MWS

In [28]:
df_test.head()

id                                               text
0  id02310  Still, as I urged our leaving Ireland with suc...
1  id24541  If a fire wanted fanning, it could readily be ...
2  id00134  And when they had broken down the frail door t...
3  id27757  While I was thinking how I should possibly man...
4  id04081  I am not sure to what limit his knowledge may ...

In [29]:
df_val.head()

index       id                                               text author
0      6  id09674  The astronomer, perhaps, at this point, took r...    EAP
1      7  id13515        The surcingle hung in ribands from my body.    EAP
2     12  id19764  Herbert West needed fresh bodies because his l...    HPL
3     15  id12799  He had escaped me, and I must commence a destr...    MWS
4     33  id11733               Even now They talked in Their tombs.    HPL

In [57]:
for i in range(df_train.values[:,1].shape[0]):
    text = df_train.iloc[i].text
    label = df_train.iloc[i].author
    print(text)
    print(label)

This process, however, afforded me no means of ascertaining the dimensions of my dungeon; as I might make its circuit, and return to the point whence I set out, without being aware of the fact; so perfectly uniform seemed the wall.
EAP
It never once occurred to me that the fumbling might be a mere mistake.
HPL
In his left hand was a gold snuff box, from which, as he capered down the hill, cutting all manner of fantastic steps, he took snuff incessantly with an air of the greatest possible self satisfaction.
EAP
How lovely is spring As we looked from Windsor Terrace on the sixteen fertile counties spread beneath, speckled by happy cottages and wealthier towns, all looked as in former years, heart cheering and fair.
MWS
Finding nothing else, not even gold, the Superintendent abandoned his attempts; but a perplexed look occasionally steals over his countenance as he sits thinking at his desk.
HPL
A youth passed in solitude, my best years spent under your gentle and feminine fosterage, has

In [27]:
class PredictAuthorDataset(torchtext.data.Dataset):
    def __init__(self, path, text_field, label_field, dfs, **kwargs):
        fields = [("text", text_field), ("label", label_field)]
        examples = []
        for i in range(dfs[path].values[:,1].shape[0]):
            text = df_train.iloc[i].text
            label = df_train.iloc[i].author
            examples.append(data.Example.fromlist([text, label], fields))
        super().__init__(examples, fields, **kwargs)

    @staticmethod
    def sort_key(ex): return len(ex.text)
    
    @classmethod
    def splits(cls, text_field, label_field, path,
               train, val, test, dfs, **kwargs):
        return super().splits(path,
            text_field=text_field, label_field=label_field,
            train=train, validation=val, test=test, dfs=dfs, **kwargs)


In [28]:
splits = PredictAuthorDataset.splits(TEXT, LABEL, '',
                             train='train',
                             val='val', test='test', dfs=df)

In [40]:
t = splits[1].examples[0]

In [41]:
t.label, ' '.join(t.text[:10])

('EAP', 'this process , however , afforded me no means of')

In [44]:
t = splits[1].examples[2]

In [45]:
t.label, ' '.join(t.text[:10])

('MWS', 'how lovely is spring as we looked from windsor terrace')

In [29]:
md2 = TextData.from_splits(PATH, splits, 1)

In [47]:
df_train[:20]

index       id                                               text author
0       0  id26305  This process, however, afforded me no means of...    EAP
1       1  id17569  It never once occurred to me that the fumbling...    HPL
2       3  id27763  How lovely is spring As we looked from Windsor...    MWS
3       4  id12958  Finding nothing else, not even gold, the Super...    HPL
4       5  id22965  A youth passed in solitude, my best years spen...    MWS
5       8  id19322  I knew that you could not say to yourself 'ste...    EAP
6       9  id00912  I confess that neither the structure of langua...    MWS
7      10  id16737  He shall find that I can feel my injuries; he ...    MWS
8      11  id16607  Here we barricaded ourselves, and, for the pre...    EAP
9      12  id19764  Herbert West needed fresh bodies because his l...    HPL
10     13  id18886  The farm like grounds extended back very deepl...    HPL
11     14  id17189   But a glance will show the fallacy of this idea.    EAP
12     15  id12799  He had escaped me, and I must commence a destr...    MWS
13     16  id08441  To these speeches they gave, of course, their ...    EAP
14     17  id13117  Her native sprightliness needed no undue excit...    MWS
15     18  id14862  I even went so far as to speak of a slightly h...    EAP
16     19  id20836  His facial aspect, too, was remarkable for its...    HPL
17     20  id11411  Now the net work was not permanently fastened ...    EAP
18     21  id08075  It was not that the sounds were hideous, for t...    HPL
19     22  id18925  On every hand was a wilderness of balconies, o...    EAP

In [30]:
dropouti, dropout, wdrop, dropoute, dropouth = np.array([0.05,0.05,0.1,0.02,0.05])*6
m3 = md2.get_model(opt_fn, 1500, bptt, emb_sz=em_sz, n_hid=nh, n_layers=nl, 
           dropouti=dropouti, dropout=dropout, wdrop=wdrop,
                       dropoute=dropoute, dropouth=dropouth)
m3.reg_fn = partial(seq2seq_reg, alpha=2, beta=1)
m3.load_encoder(f'lang-model-spooky')
#m3.load_encoder(f'/home/ubuntu/data/spooky-author-identification/weights/imdb_adam3_c1_cl10_cyc_0')

In [31]:
m3.clip=25.
lrs=np.array([1e-4,1e-3,1e-2])

In [32]:
m3.freeze_to(-1)
m3.fit(lrs/2, 1, metrics=[accuracy])

HBox(children=(IntProgress(value=0, description='Epoch', max=1), HTML(value='')))

[ 0.       1.10047  1.07873  0.42827]                            



In [33]:
log_preds, y = m3.predict_with_targs(is_test=True)

In [34]:
log_preds[:10],y[:10]

(array([[-25.58575,  -1.03932,  -2.02393,  -1.44599],
        [-26.81638,  -1.36065,  -2.21316,  -1.63146],
        [-26.80412,  -1.13825,  -2.15475,  -1.30364],
        [-27.65287,  -1.35118,  -2.01003,  -1.84277],
        [-27.91839,  -1.38737,  -2.072  ,  -1.91189],
        [-26.41141,  -1.11874,  -2.08825,  -1.78688],
        [-27.6245 ,  -1.30514,  -2.00902,  -2.02569],
        [-29.20056,  -1.37991,  -2.14771,  -1.59823],
        [-27.56208,  -1.22499,  -1.98239,  -1.60768],
        [-26.73477,  -1.2074 ,  -2.06277,  -1.34596]], dtype=float32),
 array([1, 2, 1, 2, 1, 1, 1, 1, 1, 2]))

In [35]:
preds = m3.predict()

In [48]:
res = np.argmax(log_preds, axis=1)

In [49]:
res[:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

In [50]:
y[:10]

array([1, 2, 1, 2, 1, 1, 1, 1, 1, 2])

In [51]:
pre_preds,y = m3.predict_with_targs(True)

In [52]:
preds =to_np(F.softmax(torch.from_numpy(pre_preds[:,1:])))

In [53]:
preds.shape, len(splits[2].examples)

((8391, 3), 8392)

In [54]:
preds[:10]

array([[ 0.49033,  0.18318,  0.32649],
       [ 0.45681,  0.19476,  0.34844],
       [ 0.45261,  0.16378,  0.38361],
       [ 0.46968,  0.24303,  0.28728],
       [ 0.47707,  0.24058,  0.28235],
       [ 0.52856,  0.20047,  0.27097],
       [ 0.50476,  0.24968,  0.24556],
       [ 0.44094,  0.20461,  0.35445],
       [ 0.46492,  0.21799,  0.31709],
       [ 0.43559,  0.18518,  0.37923]], dtype=float32)